In [1]:
from transformers import AutoTokenizer, AutoModelForCausalLM, GPTQConfig
import torch
model_name = "TheBloke/Tess-10.7B-v1.5b-GPTQ"

tokenizer = AutoTokenizer.from_pretrained(model_name)
model = AutoModelForCausalLM.from_pretrained(model_name, device_map="cuda:0", output_attentions=True).to("cuda")


In [2]:
from tokenizers.tools import EncodingVisualizer

viz = EncodingVisualizer(tokenizer._tokenizer)

In [7]:
# Load model directly
#from transformers import AutoTokenizer, AutoModelForCausalLM


from bertviz import head_view
from bertviz import model_view
from bertviz.neuron_view import show
# load the model
# Vicuna is an instruction-model based on Llama
#model_name = "TheBloke/Tess-10.7B-v1.5b-GPTQ" # mistralai/Mistral-7B-Instruct-v0.1
#tokenizer = AutoTokenizer.from_pretrained(model_name)
#model = AutoModelForCausalLM.from_pretrained(model_name, output_attentions=True, device_map="auto")

input_sentence = """	
Neville: Hi there, does anyone remember what date I got married on? Don: Are you serious? Neville: Dead serious. We're on vacation, and Tina's mad at me about something. I have a strange suspicion that this might have something to do with our wedding anniversary, but I have nowhere to check. Wyatt: Hang on, I'll ask my wife. Don: Haha, someone's in a lot of trouble :D Wyatt: September 17. I hope you remember the year ;)
emotions"""

input_sentence = "Miko likes Chocolate Milk. Emotion"
inputs = tokenizer.encode(input_sentence, return_tensors='pt').to("cuda")
outputs = model(inputs)
attention = outputs[-1]  # Output includes attention weights when output_attentions=True
tokens = tokenizer.convert_ids_to_tokens(inputs[0]) 



In [8]:
viz(text="Miko likes Chocolate Milk. Emotion.")

In [9]:
print(attention[0].shape)
print(attention[0][0].shape)
print(attention[0][0][0].shape)

torch.Size([1, 32, 11, 11])
torch.Size([32, 11, 11])
torch.Size([11, 11])


In [14]:
attention[0][0][0]

tensor([[1.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000,
         0.0000, 0.0000],
        [0.7612, 0.2386, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000,
         0.0000, 0.0000],
        [0.7778, 0.0806, 0.1415, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000,
         0.0000, 0.0000],
        [0.7266, 0.0543, 0.0732, 0.1459, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000,
         0.0000, 0.0000],
        [0.7500, 0.0378, 0.0274, 0.0539, 0.1306, 0.0000, 0.0000, 0.0000, 0.0000,
         0.0000, 0.0000],
        [0.7261, 0.0401, 0.0232, 0.0342, 0.0554, 0.1212, 0.0000, 0.0000, 0.0000,
         0.0000, 0.0000],
        [0.5591, 0.0569, 0.0345, 0.0313, 0.0518, 0.0900, 0.1763, 0.0000, 0.0000,
         0.0000, 0.0000],
        [0.3848, 0.0729, 0.0635, 0.0410, 0.0728, 0.0898, 0.1364, 0.1388, 0.0000,
         0.0000, 0.0000],
        [0.5718, 0.0125, 0.0183, 0.0193, 0.0138, 0.0151, 0.0158, 0.0278, 0.3057,
         0.0000, 0.0000],
        [0.4338, 0.0219, 0.0245, 0.02

In [19]:
viz(text="Miko likes Chocolate Milk. Emotion.")

In [20]:
head_view(attention, tokens)

<IPython.core.display.Javascript object>

In [15]:
result = torch.zeros(attention[0].shape).to("cuda")
for layer in attention:
    torch.add(result, layer, out=result)

In [18]:
result[0][0]

tensor([[48.0000,  0.0000,  0.0000,  0.0000,  0.0000,  0.0000,  0.0000,  0.0000,
          0.0000,  0.0000,  0.0000],
        [43.1597,  4.8417,  0.0000,  0.0000,  0.0000,  0.0000,  0.0000,  0.0000,
          0.0000,  0.0000,  0.0000],
        [44.3738,  1.9615,  1.6633,  0.0000,  0.0000,  0.0000,  0.0000,  0.0000,
          0.0000,  0.0000,  0.0000],
        [39.9263,  1.5436,  2.4486,  4.0811,  0.0000,  0.0000,  0.0000,  0.0000,
          0.0000,  0.0000,  0.0000],
        [35.9387,  0.8649,  2.0559,  6.0318,  3.1087,  0.0000,  0.0000,  0.0000,
          0.0000,  0.0000,  0.0000],
        [38.3438,  0.9330,  0.9201,  3.7467,  1.6915,  2.3657,  0.0000,  0.0000,
          0.0000,  0.0000,  0.0000],
        [39.5896,  0.4446,  0.4103,  0.9954,  1.1178,  3.4046,  2.0386,  0.0000,
          0.0000,  0.0000,  0.0000],
        [37.1255,  1.0045,  0.6250,  2.7876,  1.4512,  2.0280,  1.3746,  1.6055,
          0.0000,  0.0000,  0.0000],
        [33.8389,  0.9374,  0.6967,  2.6674,  0.8330,  1

In [17]:
result.shape

torch.Size([1, 32, 11, 11])

In [12]:
attention2 = tuple([result] + [i for i in attention[1:]])


In [66]:
attention2

(tensor([[[[48.0000,  0.0000,  0.0000,  ...,  0.0000,  0.0000,  0.0000],
           [45.7457,  2.2530,  0.0000,  ...,  0.0000,  0.0000,  0.0000],
           [43.4800,  2.1382,  2.3829,  ...,  0.0000,  0.0000,  0.0000],
           ...,
           [38.7554,  0.7176,  0.6390,  ...,  1.6464,  0.0000,  0.0000],
           [39.9022,  0.4503,  0.4166,  ...,  1.4534,  1.6614,  0.0000],
           [38.3122,  1.1326,  0.5890,  ...,  0.7079,  2.3141,  1.5070]],
 
          [[48.0000,  0.0000,  0.0000,  ...,  0.0000,  0.0000,  0.0000],
           [45.1681,  2.8312,  0.0000,  ...,  0.0000,  0.0000,  0.0000],
           [44.3584,  2.4422,  1.1989,  ...,  0.0000,  0.0000,  0.0000],
           ...,
           [41.8001,  0.9584,  0.5108,  ...,  0.7981,  0.0000,  0.0000],
           [41.2029,  0.6416,  0.5117,  ...,  1.0565,  1.2759,  0.0000],
           [39.5099,  0.8153,  0.5162,  ...,  0.4732,  1.5020,  2.0266]],
 
          [[48.0000,  0.0000,  0.0000,  ...,  0.0000,  0.0000,  0.0000],
           [4

In [67]:
head_view(attention2, tokens)

<IPython.core.display.Javascript object>

In [42]:
len(attention[0])

TypeError: len() of a 0-d tensor

In [ ]:
head_view(attention, tokens, html_action='return')
#model_view(attention, tokens, html_action='return', display_mode="light")